In [1]:
# KEYWORDS: MinHash(LSH) 

In [135]:
import numpy as np
import pandas as pd 
import string
import random
import csv
import time
import math

## Reading Data Files 

In [3]:
# The target file includes the original sequences that encodes the data. 
with open('targetBlawat et al.LDPC.txt') as f:
    reads = f.readlines()
for i in range(0,len(reads)):
    reads[i] = reads[i][0:len(reads[i])-1]
reads 

['...',
 ...]

In [4]:
np.size(reads)

9608

In [5]:
# The errors_shuffled file include the erroneous copies shuffled. 
with open('errors_shuffled.txt') as f:
    reads_err = f.readlines()
for i in range(0,len(reads_err)):
    reads_err[i] = reads_err[i][0:len(reads_err[i])-1]
# reads_err = reads_err[0:1000] 

In [6]:
np.size(reads_err)

1196656

In [7]:
# evyat.txt include the erroneous copies clustered and labeled. 
with open('evyat.txt') as f:
    reads_cl = f.readlines()
for i in range(0,len(reads_cl)):
    reads_cl[i] = reads_cl[i][0:len(reads_cl[i])-1]
reads_cl

['TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 '*****************************',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGCGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGAAACCCACACTGGGTTGTACTTGGTCAAA',
 'TGAATAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTTGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAACACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAAAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA',
 'TGAATAAAGACGAGTCCCGGAAACCCACACT

## Functions


In [166]:
def hash_fun_ind(x,a,w,l): 
    cnt = 0 
    for i in range(0,len(x)):
        if x[i] == a[cnt]:
            cnt += 1  
        else:
            cnt = 0 
        if cnt == w:
            return i-w+1 
    return -1

def hash_fun(x,a,w,l):
    ind = hash_fun_ind(x,a,w,l)
    return x[ind:min(len(x),ind+w+l)]

def ind_st(st):
    #All 3-grams: AAA,AAG,AAC,AAT,AGA,AGC,...,TTA,TTG,TTC,TTT
    # A-0, G-1, C-2, T-3
    # index of CAT = Decimal representaion of (203)
    N_q = {"A":0,"C":1,"G":2,"T":3}
    dec = 0
    for i in range(0,len(st)):
        dec += N_q[st[i]]*(4**(len(st)-i-1))
    return dec 
    
def bin_sig(x,q):
    bs = [0]*(4**q) 
    for i in range(0,len(x)-q+1):
        st = x[i:i+q]
        bs[ind_st(st)] = 1
    return bs 
        
def ham_dis(x,y):
    dis = 0
    for i in range(0,len(x)):
        if(x[i]!= y[i]):
            dis += 1
    return dis 

def rand_perm(w):
    return ''.join(random.choice('ACGT') for _ in range(w))

def merge(x,y,parent):
    parent[x]= min(parent[x],parent[y])
    parent[y]= min(parent[x],parent[y])
    
def rep_find(inp):
    temp = inp
    cnt = 0
    while(parent[temp]!=temp and cnt<10):
        cnt += 1
        temp=parent[temp]
    return temp 

def edit_dis(s1, s2):
    m=len(s1)+1
    n=len(s2)+1

    tbl = {}
    for i in range(m): tbl[i,0]=i
    for j in range(n): tbl[0,j]=j
    for i in range(1, m):
        for j in range(1, n):
            cost = 0 if s1[i-1] == s2[j-1] else 1
            tbl[i,j] = min(tbl[i, j-1]+1, tbl[i-1, j]+1, tbl[i-1, j-1]+cost)

    return tbl[i,j]

def find_in_arr(el,parent):
    cnt = 0
    for i in range(0,len(parent)):
        if parent[i] == el: 
            cnt += 1 
    return cnt 
        
        
    

In [107]:
rand_perm(4)

'TCTG'

In [108]:
hash_fun("abc","c",1,2)

'c'

In [109]:
hash_fun(reads_err[0],"GA",2,2)

'GAGA'

In [110]:
bin_sig("TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA",2)

[1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1]

In [111]:
ham_dis("ACT","ATG")

2

In [179]:
q =  3
x = "CTATCTTCACAAATACCTGTTCCTGCTCGCCTAGTTCTGCCTGGACGACT"
y = "TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA"
ham_dis(bin_sig(x,q),bin_sig(y,q))

28

In [180]:
edit_dis(x,y)

26

In [150]:
x = "TGAATAAAAAGACGAGTCCCGGAAACCCACACTGGTTGTACTTGGTCAAA"
y = "TGAATAAAAAGACTCCCGGAAACACACTGGTTGTACTTGGTCAAA"
ham_dis(bin_sig(x,q),bin_sig(y,q))

7

In [151]:
edit_dis(x,y)

5

## A Local Computaion Step of the Algorithm 

In [361]:
# GLOBAL CLUTERING DENOTED BY C_til
# Parent stores cluster id corresponding to each read
# Disjoint set Union Problem 

C_til  = [0]*(len(reads_err))
parent = [0]*(len(reads_err))
for i in range(0,len(reads_err)):
    C_til[i] = (i,reads_err[i]) 
    parent[i] = i
C_til

[(0, 'GGGAGACTCGCAATATAGAATACATACTTGACGTAGCAGTCTTTTATGGA'),
 (1, 'GCAGAGGATTCCTGGGCCGCTGATCCAGTTAACACATGTGATGGCCACAC'),
 (2, 'ATCATGGTCAAGAGGTTGATTTCGATCAACTGAGCATCCCGTCTGCGGTTG'),
 (3, 'TCATCTCTAAGCGGCGAGCTACAATCCGCTCCGAAGCGCTCCCTAGTAAC'),
 (4, 'ATCGGTACCCTCAAACTAGCATGGAACTTCTATCGGATCGCTGGCAGATA'),
 (5, 'GAGTGGTCTCGAAGACATGCAACCCAGCACATACAACACCCGAGCGGTAAT'),
 (6, 'TCGCTGTTAAATCGTCACACCACGTCAACTATACGTAGTACCTCCCTGAC'),
 (7, 'AGGCCGCTTATAGAGGACGTCTGTTCAGGTCATCGGTATGTCTCGTGAG'),
 (8, 'GTATCCTACTCAGCTTAAGGGGCACACGCCAGCGCATGCACACACTGCTCC'),
 (9, 'CTATCTTCACAAATACCTGTTCCTGCTCGCCTAGTTCTGCCTGGACGACT'),
 (10, 'CTACCCAGTAGCGCATACGTTAGCTATTATGAGGCTTGATGGTCGAAGTGG'),
 (11, 'TAGGGTTGCATCTTTGCATAATAAACTTGGCCATAGCGTGTCTCCCTCCC'),
 (12, 'GTTGTCAAGGGACATGGATTTGCCCCTCGGGATGTATTCAGGGATTCA'),
 (13, 'CGCATTGGGTAGGACCAACATCTGCTCCGCATGTGAGGGTTGATATGATG'),
 (14, 'GGTTATGGCTACTTGTCTACGGTGACTAGTTGACCGCTTAGCCTCCCGGT'),
 (15, 'CCATGTGAGGAGACTGGCTACCTCGGCAGGTAAGTTCGGGCATAACCGATT'),
 (16, 'ACTTGAAACGTAGACGCACGATATC

In [362]:
# Step 1: Sample a Hash Function 
# Step 2: Compute Hash of a random representative of each cluster 
# Step 3: Merge two clusters with same hash if ham_dis(bin_sig(x),bin_sig(y)) <= th_high
a = "GGA"
w = len(a)
l = math.ceil(math.log(1196656,4))
hash_C_til = [0]*(len(reads_err))

for i in range(0,len(C_til)):
    hash_C_til[i] = (i,hash_fun(C_til[i][1],a,w,l))

In [363]:
l = math.ceil(math.log(1196656,4))
l

11

In [364]:
hash_C_til

[(0, 'GGA'),
 (1, 'GGATTCCTGGGCCG'),
 (2, ''),
 (3, ''),
 (4, 'GGAACTTCTATCGG'),
 (5, ''),
 (6, ''),
 (7, 'GGACGTCTGTTCAG'),
 (8, ''),
 (9, 'GGACGACT'),
 (10, ''),
 (11, ''),
 (12, 'GGATTTGCCCCTCG'),
 (13, 'GGACCAACATCTGC'),
 (14, ''),
 (15, 'GGAGACTGGCTACC'),
 (16, ''),
 (17, 'GGATACGCAAAATA'),
 (18, 'GGACTCATATGTGC'),
 (19, 'GGAAGACCTGCGCA'),
 (20, ''),
 (21, ''),
 (22, ''),
 (23, 'GGACGTTTTAAAAA'),
 (24, ''),
 (25, 'GGACGCAGCGCATG'),
 (26, ''),
 (27, 'GGAGCGCCAATCGT'),
 (28, ''),
 (29, 'GGAGTACTGTTGGA'),
 (30, 'GGAACTTGAGCGTT'),
 (31, ''),
 (32, 'GGAAGTGATCGCCG'),
 (33, 'GGAGCCTCAAGATA'),
 (34, 'GGACCTTACGTCCA'),
 (35, 'GGATTGCACTCATA'),
 (36, ''),
 (37, ''),
 (38, ''),
 (39, 'GGAAACATTCAAT'),
 (40, ''),
 (41, 'GGAATAAA'),
 (42, ''),
 (43, ''),
 (44, 'GGACGATTCCCCAG'),
 (45, ''),
 (46, 'GGAGATG'),
 (47, 'GGATGACTTGCGCT'),
 (48, 'GGAATTCGATTCCT'),
 (49, 'GGATGGGAACACAA'),
 (50, ''),
 (51, 'GGATTCCTGGGCCG'),
 (52, ''),
 (53, ''),
 (54, ''),
 (55, ''),
 (56, ''),
 (57, ''),
 (58, ''),


In [365]:
len("GGACGCCAATCGGG")

14

In [366]:
hash_C_til.sort(key=lambda x:x[1])
hash_C_til

[(2, ''),
 (3, ''),
 (5, ''),
 (6, ''),
 (8, ''),
 (10, ''),
 (11, ''),
 (14, ''),
 (16, ''),
 (20, ''),
 (21, ''),
 (22, ''),
 (24, ''),
 (26, ''),
 (28, ''),
 (31, ''),
 (36, ''),
 (37, ''),
 (38, ''),
 (40, ''),
 (42, ''),
 (43, ''),
 (45, ''),
 (50, ''),
 (52, ''),
 (53, ''),
 (54, ''),
 (55, ''),
 (56, ''),
 (57, ''),
 (58, ''),
 (60, ''),
 (62, ''),
 (63, ''),
 (64, ''),
 (69, ''),
 (70, ''),
 (72, ''),
 (75, ''),
 (76, ''),
 (77, ''),
 (79, ''),
 (80, ''),
 (81, ''),
 (84, ''),
 (85, ''),
 (86, ''),
 (87, ''),
 (88, ''),
 (89, ''),
 (90, ''),
 (91, ''),
 (92, ''),
 (93, ''),
 (95, ''),
 (98, ''),
 (100, ''),
 (102, ''),
 (104, ''),
 (106, ''),
 (107, ''),
 (110, ''),
 (111, ''),
 (112, ''),
 (113, ''),
 (114, ''),
 (118, ''),
 (119, ''),
 (120, ''),
 (121, ''),
 (122, ''),
 (124, ''),
 (129, ''),
 (130, ''),
 (132, ''),
 (133, ''),
 (136, ''),
 (137, ''),
 (138, ''),
 (143, ''),
 (144, ''),
 (145, ''),
 (146, ''),
 (149, ''),
 (150, ''),
 (151, ''),
 (152, ''),
 (154, ''),
 (156

In [367]:
q = 3
th_high = 12
th_low  = 8
r = 6
cnt = 0

start = time.time()
for i in range(0,len(reads_err)-1):
    if(hash_C_til[i][1] == ""):
        continue 
    else:
        if hash_C_til[i][1] == hash_C_til[i+1][1]:
#             if rep_find(i) == rep_find(i+1):
#                 continue 
            x = reads_err[hash_C_til[i][0]]
            y = reads_err[hash_C_til[i+1][0]]
            if((ham_dis(bin_sig(x,q),bin_sig(y,q)) <= th_low) or ((ham_dis(bin_sig(x,q),bin_sig(y,q)) <= th_high) and edit_dis(x,y)<=r)):
                cnt +=  1
                merge(hash_C_til[i][0],hash_C_til[i+1][0],parent)
print(cnt)

end = time.time()
print(end-start)

394295
78.92541694641113


In [ ]:
# * 12,8,6,73
# 16,8,6,74
# * 12,6,6,113
# 10,6,6,111
# 10,5,5,146
# 8,5,3,133

In [156]:
parent

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 1,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 48,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 59,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 140,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,
 1

In [157]:
rep_find(67)

48

# Clustering Algorithm

In [317]:
with open('errors_shuffled.txt') as f:
    reads_err = f.readlines()
for i in range(0,len(reads_err)):
    reads_err[i] = reads_err[i][0:len(reads_err[i])-1]
    
C_til  = [0]*(len(reads_err))
parent = [0]*(len(reads_err))
for i in range(0,len(reads_err)):
    C_til[i] = (i,reads_err[i]) 
    parent[i] = i

local_comm = 200
q = 3
th_high = 12
th_low  = 6
r = 6
w = 3
l = math.ceil(math.log(np.size(reads_err),4))


for lcl_step in range(0,local_comm):
    a = rand_perm(w)
    hash_C_til = [0]*(len(reads_err))

    for i in range(0,len(C_til)):
        hash_C_til[i] = (i,hash_fun(C_til[i][1],a,w,l))
    
    hash_C_til.sort(key=lambda x:x[1])

    cnt =0
    for i in range(0,len(reads_err)-1):
        if(hash_C_til[i][1] == ""):
            continue 
        else:
            if hash_C_til[i][1] == hash_C_til[i+1][1]:
                if rep_find(i) == rep_find(i+1):
                    continue 
                x = reads_err[hash_C_til[i][0]]
                y = reads_err[hash_C_til[i+1][0]]
                if((ham_dis(bin_sig(x,q),bin_sig(y,q)) <= th_low) or ((ham_dis(bin_sig(x,q),bin_sig(y,q)) <= th_high) and edit_dis(x,y)<=r)):
                    cnt +=  1
                    merge(hash_C_til[i][0],hash_C_til[i+1][0],parent)
                    
    print(lcl_step,cnt)

0 377621
1 423752
2 416294
3 418611
4 367339
5 441089
6 424892
7 446859
8 394491
9 435337
10 435544
11 393635
12 480165
13 432196
14 441076
15 417777
16 434322
17 423358
18 446849
19 431148
20 445689
21 440873
22 405800
23 388751
24 410425
25 450381
26 410425
27 399949
28 445285
29 501924
30 410425
31 445285
32 367323
33 423713
34 446848
35 445921
36 399949
37 393633
38 429479
39 394488
40 480163
41 461186
42 451153
43 412134
44 392064
45 445105
46 462448
47 405500
48 432194
49 405500
50 359968
51 449513
52 409402
53 424881
54 392064
55 388751
56 461186
57 429479
58 403014
59 418588
60 428090
61 435541
62 435541
63 424881
64 416262
65 443715
66 388751
67 406515
68 480163
69 445921
70 388751
71 410425
72 432194
73 445689
74 403014
75 370535
76 445105
77 446848
78 435541
79 430807
80 444547
81 432194
82 501924
83 423357
84 367323
85 501924
86 430807
87 403014
88 444547
89 348804
90 446548
91 429479
92 434322
93 462448
94 445921
95 435333
96 430807
97 418588
98 435333
99 416262
100 450381

In [318]:
parent

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 1,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 48,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 59,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 140,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 136,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,
 1

In [319]:
np.savetxt("parent_file_12_6_6.txt", np.array(parent), fmt="%s")

In [176]:
find_in_arr(48,parent)

11

In [320]:
def display_parent(parent):
    clstr = {}
    for i in range(0,len(parent)):
        clstr[i]=[]
    for i in range(0,len(parent)):
        clstr[rep_find(i)].append(i)
    return clstr

In [322]:
clustering = display_parent(parent)

In [323]:
clustering

{0: [0,
  2648,
  6403,
  6755,
  20953,
  23287,
  26757,
  32312,
  32747,
  33354,
  42180,
  56123,
  64600,
  65175,
  70295,
  72516,
  73272,
  75751,
  90416,
  98595,
  103065,
  105979,
  106216,
  111840,
  115263,
  119932,
  126913,
  127369,
  145286,
  147167,
  153686,
  164979,
  175594,
  184042,
  188823,
  188865,
  198350,
  203099,
  203208,
  228822,
  233523,
  237321,
  242114,
  244167,
  252484,
  255188,
  295613,
  302430,
  310175,
  312198,
  316207,
  318801,
  321787,
  323557,
  331386,
  338581,
  340377,
  350048,
  350861,
  351475,
  355913,
  361299,
  362009,
  362419,
  365650,
  366109,
  367917,
  368476,
  386834,
  390395,
  393609,
  397907,
  399985,
  408964,
  412118,
  422939,
  423164,
  437596,
  438208,
  439091,
  443819,
  445700,
  456484,
  460850,
  461807,
  466417,
  476558,
  484841,
  510675,
  510727,
  512344,
  513613,
  520541,
  520644,
  523703,
  524649,
  538909,
  539249,
  554203,
  555536,
  570773,
  582421,
  59

In [324]:
# random.choice(clustering_200[0])
len(clustering[2])

117

In [325]:
ham_dis(bin_sig(reads_err[0],q),bin_sig(reads_err[967736],q))

0

In [329]:
with open('errors_shuffled.txt') as f:
    reads_err = f.readlines()
for i in range(0,len(reads_err)):
    reads_err[i] = reads_err[i][0:len(reads_err[i])-1]
    
C_til  = [0]*(len(reads_err))
parent2 = [0]*(len(reads_err))
for i in range(0,len(reads_err)):
    C_til[i] = (i,reads_err[i]) 
    parent2[i] = i

local_comm = 200
q = 3
th_high = 16
th_low  = 8
r = 6
w = 3
l = math.ceil(math.log(np.size(reads_err),4))


for lcl_step in range(0,local_comm):
    a = rand_perm(w)
    hash_C_til = [0]*(len(reads_err))

    for i in range(0,len(C_til)):
        hash_C_til[i] = (i,hash_fun(C_til[i][1],a,w,l))
    
    hash_C_til.sort(key=lambda x:x[1])

    cnt =0
    for i in range(0,len(reads_err)-1):
        if(hash_C_til[i][1] == ""):
            continue 
        else:
            if hash_C_til[i][1] == hash_C_til[i+1][1]:
                if rep_find(i) == rep_find(i+1):
                    continue 
                x = reads_err[hash_C_til[i][0]]
                y = reads_err[hash_C_til[i+1][0]]
                if((ham_dis(bin_sig(x,q),bin_sig(y,q)) <= th_low) or ((ham_dis(bin_sig(x,q),bin_sig(y,q)) <= th_high) and edit_dis(x,y)<=r)):
                    cnt +=  1
                    merge(hash_C_til[i][0],hash_C_til[i+1][0],parent2)
                    
    print(lcl_step,cnt)

0 431517
1 481094
2 450231
3 426732
4 440899
5 411124
6 466213
7 394295
8 395120
9 450231
10 412803
11 446020
12 432918
13 445230
14 406506
15 422889
16 422889
17 400611
18 447337
19 403698
20 445230
21 418446
22 466213
23 418446
24 441791
25 394295
26 440899
27 436282
28 441565
29 435856
30 481493
31 447652
32 446020
33 419286
34 444459
35 425539
36 441361
37 360568
38 378221
39 418446
40 411124
41 412803
42 430162
43 389384
44 447652
45 419286
46 412803
47 424390
48 436127
49 436127
50 411124
51 451151
52 441565
53 424063
54 422889
55 502815
56 389384
57 446020
58 424390
59 426732
60 450231
61 410127
62 430162
63 481493
64 422889
65 466213
66 447337
67 367925
68 453530
69 481094
70 451151
71 451940
72 445230
73 451151
74 406159
75 378221
76 440899
77 481094
78 441565
79 389384
80 424390
81 394860
82 445868
83 367925
84 394295
85 443819
86 445230
87 407181
88 406506
89 453530
90 430162
91 447652
92 445230
93 450231
94 433902
95 446674
96 431863
97 481493
98 418446
99 435856
100 444459

In [331]:
parent2

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 1,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 48,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 59,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 140,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 136,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,
 1

In [332]:
np.savetxt("parent_file_16_8_6.txt", np.array(parent2), fmt="%s")

In [333]:
clustering2 = display_parent(parent2)
clustering2

{0: [0,
  2648,
  6403,
  6755,
  20953,
  23287,
  26757,
  32312,
  32747,
  33354,
  42180,
  56123,
  64600,
  65175,
  70295,
  72516,
  73272,
  75751,
  90416,
  98595,
  103065,
  105979,
  106216,
  111840,
  115263,
  119932,
  126913,
  127369,
  145286,
  147167,
  153686,
  164979,
  175594,
  184042,
  188823,
  188865,
  198350,
  203099,
  203208,
  228822,
  233523,
  237321,
  242114,
  244167,
  252484,
  255188,
  295613,
  302430,
  310175,
  312198,
  316207,
  318801,
  321787,
  323557,
  331386,
  338581,
  340377,
  350048,
  350861,
  351475,
  355913,
  361299,
  362009,
  362419,
  365650,
  366109,
  367917,
  368476,
  386834,
  390395,
  393609,
  397907,
  399985,
  408964,
  412118,
  422939,
  423164,
  437596,
  438208,
  439091,
  443819,
  445700,
  456484,
  460850,
  461807,
  466417,
  476558,
  484841,
  510675,
  510727,
  512344,
  513613,
  520541,
  520644,
  523703,
  524649,
  538909,
  539249,
  554203,
  555536,
  570773,
  582421,
  59

In [334]:
len(clustering_200.keys())

1196656

In [350]:
cnt = 0 
for i in range(0,len(clustering)):
    if(len(clustering2[i]) !=len(clustering[i])):
        cnt += 1
cnt

0

In [343]:
len(clustering)

1196656